# Quick Start

After installing and configuring QESEM, you can create your first QESEM job. Before diving into the API documentation, provided below is a full example of how to use it. This script runs a simple QESEM job on IBM QPU:

## Setup

In [ ]:
!pip install -U --upgrade-strategy eager qedma-api
!pip install qiskit

In [1]:
import qedma_api
import qiskit
import datetime
from qedma_api import ExpectationValues

# configuration
qedma_api_token = "<Qedma api token>"
ibm_instance = "<IBM instance ID>"

qedma_client = qedma_api.Client(api_token = qedma_api_token)
provider = qedma_api.IBMQProvider(
    instance = ibm_instance,
)
qedma_client.set_provider(provider)

## Create a QESEM job 
Create a circuit using qiskit

In [2]:
circuit = qiskit.QuantumCircuit(5)
circuit.cx(0, 1)
circuit.cx(2, 3)
circuit.cx(1, 2)
circuit.cx(3, 4)

We will use two observables

$$ \frac{1}{5}\sum_{q=0}^4 Z_{q} \quad \text{and}\quad Z_0 Z_1 + 0.5 X_1 Z_4 $$

We pass them as two Qiskit `SparsePauliOp` instances

In [3]:
avg_magnetization = qiskit.quantum_info.SparsePauliOp.from_sparse_list(
    [("Z", [q], 1 / 5) for q in range(5)], num_qubits=5
)
other_observable = qiskit.quantum_info.SparsePauliOp.from_sparse_list(
    [("ZZ", [0, 1], 1.0), ("XZ", [1, 4], 0.5)], num_qubits=5
)

Create a new QESEM job

In [4]:
job = qedma_client.create_job(
    circuit = circuit,
    observables = [avg_magnetization, other_observable],
    observables_metadata = [
        qedma_api.ObservableMetadata(description = "avg_magnetization"),
        qedma_api.ObservableMetadata(description = "other_observable")
    ],
    empirical_time_estimation = True,
    precision = 0.1,
    backend = "fake_fez",
    description = "my qesem job",
)

2025-07-01 14:32:11.027 | INFO     | Submitting new job
2025-07-01 14:32:12.748 | INFO     | [60ff19853e944112a44e655a5ecb2fb0] New job created


<div class="admonition note">
    <p class="admonition-title">Note</p>
    <p style="padding-top:10px" >
       The <code>precision</code> signifies the acceptable error on the expectation values of the observables in absolute value. Namely, the QPU runtime for mitigation will be determined to provide output values for all the observables of interest that fall within a <code>1σ</code> confidence interval of the target precision. If multiple observables are provided, the mitigation will run until the target precision is reached for each of the input observables.
    </p>
</div>

<div class="admonition note">
    <p class="admonition-title">Note</p>
    <p style="padding-top:10px" >
       When the QESEM job completes, an email notification is sent to the job creator. In some cases, the email might end up in the spam or quarantine folder. If that happens, simply mark the sender as trusted, this should prevent the issue from occurring again. If you prefer not to receive email notifications, set <a href="/reference/#qedma_api.models.JobDetails.enable_notifications"><code>enable_notifications = False</code></a> when creating the QESEM job.
    </p>
</div>

## Estimate QPU time

Once the job is created, a QPU time estimation is initiated. Use the function `qedma_client.wait_for_estimation()` which waits until the estimation is complete and returns the time estimation. (There are two types of time estimation, learn more [here](/advanced_settings/#qpu-time-estimation))

In [6]:
qedma_client.wait_for_time_estimation(job_id = job.job_id)

2025-07-01 14:36:01.736 | INFO     | [60ff19853e944112a44e655a5ecb2fb0] Time estimation: [5.0 minutes]


datetime.timedelta(seconds=300)

<div class="admonition note">
    <p class="admonition-title">Note</p>
    <p style="padding-top:10px" >
       In general, the problem is BQP-hard but QESEM's heuristic time estimation has polynomial scaling. The heuristic estimation is best for a Pauli string observable while for more complex observables it gives an upper bound. During the estimation, job execution, QESEM does not use the heuristic time estimation, but a more reliable estimation based on empirical data to ensure minimal QPU-time usage.
    </p>
</div>

## Start Execution

Initiate the execution of the QESEM job:

In [7]:
qedma_client.start_job(
    job_id = job.job_id, 
    max_qpu_time = datetime.timedelta(minutes = 5)
)

2025-07-01 14:36:11.772 | INFO     | [60ff19853e944112a44e655a5ecb2fb0] Starting job


<div class="admonition note">
    <p class="admonition-title">Note</p>
    <p style="padding-top:10px" >
       <code>max_qpu_time</code> is mandatory when starting a QESEM job. It allows you to limit the QPU time, specified in seconds, to be used for the entire QESEM process. Since the final QPU time required to reach the target accuracy is determined dynamically during the QESEM job, this parameter enables you to limit the cost of the experiment. If the dynamically-determined QPU time is shorter than the time allocated by the user, this parameter will not affect the experiment. After the time limit it reached, QESEM stops sending new circuits. Circuits that have already been sent continue running (so the total time may surpass the limit by up to 30 minutes), and the user receives the processed results from the circuits that ran up to that point.
    </p>
</div>



Even before the QESEM job completes, we let you track the job's progress and access intemadiate mitigation results. The QESEM job executes multiple batches of characterization, calibration and mitigation circuits. During the mitigation stage, QESEM calculates intermediate mitigation results that gradually converge to the final mitigated result. Use the `qedma_client.wait_for_job_complete()` function to get all this data printed automatically, it will wait until the job completes.


In [8]:
job = qedma_client.wait_for_job_complete(job_id = job.job_id)

2025-07-01 14:36:18.124 | INFO     | [60ff19853e944112a44e655a5ecb2fb0] step: [Queued]
2025-07-01 14:36:18.125 | INFO     | [60ff19853e944112a44e655a5ecb2fb0] step: [Initial Transpilation]
2025-07-01 14:36:18.126 | INFO     | [60ff19853e944112a44e655a5ecb2fb0] step: [Qubit Selection]
2025-07-01 14:37:01.916 | INFO     | [60ff19853e944112a44e655a5ecb2fb0] step: [Calibration]
2025-07-01 14:37:01.918 | INFO     | [60ff19853e944112a44e655a5ecb2fb0] step: [Characterization]
2025-07-01 14:38:17.658 | INFO     | [60ff19853e944112a44e655a5ecb2fb0] step: [Batch Mitigation #1]


2025-07-01 14:39:54.997 | INFO     | [60ff19853e944112a44e655a5ecb2fb0] Final results: [[<SparseObservable with 5 terms on 5 qubits: (0.2+0j)(Z_0) + (0.2+0j)(Z_1) + (0.2+0j)(Z_2) + (0.2+0j)(Z_3) + (0.2+0j)(Z_4)>: (1.000676575536313 ± 0.0033883682697840594), <SparseObservable with 2 terms on 5 qubits: (1+0j)(Z_1 Z_0) + (0.5+0j)(Z_4 X_1)>: (1.009224816958378 ± 0.0020171731955879392)]]


<div class="admonition note">
    <p class="admonition-title">Note</p>
    <p style="padding-top:10px" >
       The QESEM results include an expectation value and an error bar for each requested observable. These values are updated throughout the QESEM process and finalized when the job status is <code>SUCCEEDED</code>. The error bars are derived empirically from the standard deviation of the QESEM mitigation circuits executed on the QPU. They represent the statistical uncertainty of the QESEM result within the allocated QPU time – specifically, the standard deviation of its distribution around the ideal expectation value.
    </p>
</div>


# Next Steps
- Learn about QESEM's [Advanced Settings](/advanced_settings), which allow you to control QESEM execution to better fit your use case.
- Learn how to access QESEM job [Execution Metrics](/execution_metrics), such as noisy results and the total number of shots used during execution.